In [2]:
import wfdb
import os
import tensorflow as tf
import matplotlib.pyplot as plt
from python_speech_features.base import mfcc
from sklearn.model_selection import train_test_split
from tensorflow.keras.layers import GRU
import numpy as np
from scipy.ndimage import zoom
import pandas as pd
from sklearn.model_selection import GroupShuffleSplit
import tensorflow as tf
import pywt
from gen_wavelet_images import generate_wavelet_images as gen_wav
import scipy.signal


In [27]:
import matplotlib.pyplot as plt

In [2]:
import concurrent.futures
import multiprocessing as mp
mp.set_start_method("spawn")

In [3]:
# RESAMPLE
FRAME_TIME = 5 # The frame time (in seconds) to divide the signals into equally sized samples
FRAME_OVERLAP = 0 # The frame overlap (in seconds)
RESAMPLE_FACTOR = 1
TRAIN_SIZE = 0.7
fr = 300
classification_path = r'.\physionet2017_ecg\REFERENCE-v3.csv'
records_folder=r'.\physionet2017_ecg\training2017'

## Data Loading and preprocessing

Loading signals, info and resampling

In [4]:
def read_files(folder = '', extension = ".wav"):
    cont = 0
    signal_dict_list = []
    for filename in os.listdir(folder):
        
        if filename.endswith(".hea") : 
            record_name = filename[:-4]
            record = wfdb.rdheader(os.path.join(folder, record_name))
            signal = wfdb.rdrecord(os.path.join(folder, record_name)).__dict__['p_signal'][:][::RESAMPLE_FACTOR]
            fs = record.__dict__['fs']
            
            cont +=1
            #print(record.__dict__)
            #patient_id = record_name.split('_')[0]
            #signal_dict = {'patient_id': patient_id, 'record_name':record_name, 'fs': fs, 'sig_len':record.__dict__['sig_len'], 'signal': signal}
            signal_dict = { 'record_name':record_name, 'fs': fs, 'sig_len':record.__dict__['sig_len'], 'signal': signal}
           
            signal_dict_list.append(signal_dict)
            
            
            
    return pd.DataFrame(signal_dict_list)

In [5]:
df = read_files(folder=records_folder)

In [6]:
classification = pd.read_csv(classification_path, names = ['record_name', 'class'])
classification

record_name class
0         A00001     N
1         A00002     N
2         A00003     N
3         A00004     A
4         A00005     A
...          ...   ...
8523      A08524     N
8524      A08525     O
8525      A08526     N
8526      A08527     N
8527      A08528     N

[8528 rows x 2 columns]

### Preprocessing


Dropping class = ~ (noisy) since no classification is provided

In [7]:
classification=classification[classification['class']!='~']

In [8]:
classification['class']=classification['class'].apply(lambda x: 0 if x == 'N' else 1)
classification

<ipython-input-8-9ffcc234a887>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  classification['class']=classification['class'].apply(lambda x: 0 if x == 'N' else 1)


record_name  class
0         A00001      0
1         A00002      0
2         A00003      0
3         A00004      1
4         A00005      1
...          ...    ...
8523      A08524      0
8524      A08525      1
8525      A08526      0
8526      A08527      0
8527      A08528      0

[8249 rows x 2 columns]

In [9]:
df

record_name   fs  sig_len  \
0         A00001  300     9000   
1         A00002  300     9000   
2         A00003  300    18000   
3         A00004  300     9000   
4         A00005  300    18000   
...          ...  ...      ...   
8523      A08524  300     9000   
8524      A08525  300     9000   
8525      A08526  300    10904   
8526      A08527  300     9000   
8527      A08528  300     9000   

                                                 signal  
0     [[-0.127], [-0.162], [-0.197], [-0.229], [-0.2...  
1     [[0.128], [0.157], [0.189], [0.226], [0.25], [...  
2     [[0.056], [0.073], [0.085], [0.093], [0.1], [0...  
3     [[0.519], [0.619], [0.723], [0.827], [0.914], ...  
4     [[-0.188], [-0.239], [-0.274], [-0.316], [-0.3...  
...                                                 ...  
8523  [[-0.104], [-0.127], [-0.144], [-0.154], [-0.1...  
8524  [[-0.121], [-0.197], [-0.288], [-0.39], [-0.49...  
8525  [[-0.202], [-0.235], [-0.272], [-0.305], [-0.3...  
8526  [[-0.227], [-0.297], [-0.374], [-0.449], [-0.5...  
8527  [[-0.237], [-0.286], [-0.338], [-0.39], [-0.42...  

[8528 rows x 4 columns]

In [10]:
classification['class'].value_counts()

0    5076
1    3173
Name: class, dtype: int64

#### Merging with the records df

In [11]:
df=df.merge(classification, on='record_name', how = 'right')

In [12]:
df

record_name   fs  sig_len  \
0         A00001  300     9000   
1         A00002  300     9000   
2         A00003  300    18000   
3         A00004  300     9000   
4         A00005  300    18000   
...          ...  ...      ...   
8244      A08524  300     9000   
8245      A08525  300     9000   
8246      A08526  300    10904   
8247      A08527  300     9000   
8248      A08528  300     9000   

                                                 signal  class  
0     [[-0.127], [-0.162], [-0.197], [-0.229], [-0.2...      0  
1     [[0.128], [0.157], [0.189], [0.226], [0.25], [...      0  
2     [[0.056], [0.073], [0.085], [0.093], [0.1], [0...      0  
3     [[0.519], [0.619], [0.723], [0.827], [0.914], ...      1  
4     [[-0.188], [-0.239], [-0.274], [-0.316], [-0.3...      1  
...                                                 ...    ...  
8244  [[-0.104], [-0.127], [-0.144], [-0.154], [-0.1...      0  
8245  [[-0.121], [-0.197], [-0.288], [-0.39], [-0.49...      1  
8246  [[-0.202], [-0.235], [-0.272], [-0.305], [-0.3...      0  
8247  [[-0.227], [-0.297], [-0.374], [-0.449], [-0.5...      0  
8248  [[-0.237], [-0.286], [-0.338], [-0.39], [-0.42...      0  

[8249 rows x 5 columns]

In [13]:
df['class'].value_counts()

0    5076
1    3173
Name: class, dtype: int64

### Train test split

Splits the data in train test, not leaking the same subject on both sets

In [14]:
X_train, X_test, y_train, y_test, train_names, test_names = train_test_split(df['signal'].tolist(), df['class'].tolist(), df['record_name'].tolist(), test_size=0.3, stratify=df['class'], random_state=42)

In [15]:
frame_time = FRAME_TIME # time in seconds desired
frame_overlap = FRAME_OVERLAP # overlap in seconds

frame_length = int (fr * frame_time)
frame_step = int(frame_length - fr * frame_overlap)


In [16]:
type(X_train)

list

In [17]:
def create_frames ( pcg, y, groups):
    f_y_train = []
    X_pcg = []
    record_id = []
    for index in range (len (pcg)):
        print (index)
        pcg_signal = np.hstack(np.nan_to_num(pcg[index], copy=True, nan=0.0, posinf=None, neginf=None))
        #pcg_frames = segment_signal(pcg_signal, model)
        pcg_frames = tf.signal.frame(pcg[index].T, frame_length= frame_length, frame_step = frame_step, pad_end=False).numpy().tolist()[0]
        #print(pcg_frames)
        X_pcg.extend(pcg_frames)
        
        f_y_train = f_y_train + [y[index]] * len (pcg_frames)
        record_id.extend([groups[index]]* len (pcg_frames))
    return  X_pcg, f_y_train, record_id


In [18]:
X_train_ecg, f_y_train, record_id = create_frames ( X_train, y_train, train_names)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064


3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715


5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349
5350
5351
5352
5353
5354
5355
5356
5357
5358
5359
5360
5361
5362


In [19]:
X_test_ecg, f_y_test, record_id_test = create_frames ( X_test, y_test, test_names)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070


In [20]:
record_id

['A06047',
 'A06047',
 'A06047',
 'A06047',
 'A06047',
 'A06047',
 'A06729',
 'A06729',
 'A06729',
 'A06729',
 'A06729',
 'A06729',
 'A06729',
 'A06729',
 'A02642',
 'A02642',
 'A02642',
 'A02642',
 'A02642',
 'A02642',
 'A03493',
 'A03493',
 'A03493',
 'A03493',
 'A03493',
 'A03493',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A03391',
 'A07249',
 'A07249',
 'A07249',
 'A07249',
 'A07249',
 'A07249',
 'A06066',
 'A06066',
 'A06066',
 'A06066',
 'A06066',
 'A06066',
 'A04740',
 'A04740',
 'A04740',
 'A04740',
 'A04740',
 'A04740',
 'A04471',
 'A04471',
 'A04471',
 'A04471',
 'A04471',
 'A04471',
 'A05279',
 'A05279',
 'A05279',
 'A05279',
 'A05279',
 'A05279',
 'A02351',
 'A02351',
 'A02351',
 'A02351',
 'A02351',
 'A02351',
 'A04404',
 'A04404',
 'A04404',
 'A04404',
 'A04404',
 'A04404',
 'A06838',
 'A06838',
 'A06838',
 'A06838',
 'A06838',
 'A06838',
 'A08082',
 'A08082',
 'A08082',
 'A00254',
 'A00254',

Reshaping

In [21]:


X_test_ecg = np.array(X_test_ecg)
X_train_ecg = np.array(X_train_ecg)

X_test_ecg = np.nan_to_num(X_test_ecg, copy=True, nan=0.0, posinf=None, neginf=None)
X_train_ecg  = np.nan_to_num(X_train_ecg, copy=True, nan=0.0, posinf=None, neginf=None)


X_test_ecg = X_test_ecg.reshape(X_test_ecg.shape[0], X_test_ecg.shape[1], 1)
X_train_ecg = X_train_ecg.reshape(X_train_ecg.shape[0], X_train_ecg.shape[1], 1)




#### Standardization

In [22]:
def standardize_signals(signals):
    standardized_signals = []
    for signal in signals:
        mean = np.mean(signal)
        #print (mean)
        std = np.std(signal)
        standardized_signal = (signal - mean) / std
        standardized_signals.append(standardized_signal)
    return np.array(standardized_signals)

In [23]:
X_train_ecg = standardize_signals(X_train_ecg)
X_test_ecg = standardize_signals(X_test_ecg)

In [24]:
record_id_test.index('A08105')

751

### Bandpass filter 



In [33]:
plt.plot(X_train_ecg[1000])
plt.savefig('ecg_train.png')
plt.close()

In [25]:

def butter_bandpass(lowcut, highcut, fs, order, signals):
    # Normalized cutoff frequencies
    b, a = scipy.signal.butter(order, [lowcut, highcut], btype='band', fs=fs)
    
    filtered_signals = []
    for s in signals:
        s= np.ravel(s)
        #print (s.shape)
        y = scipy.signal.filtfilt(b, a, s)
        
        filtered_signals.append(y)
    return np.array(filtered_signals)


In [26]:
def remove_spikes(signals, window_size=0.5, fs=2000):
    # Convert window size from seconds to samples
    window_size = int(window_size * fs)
    filtered_signals = []
    i = 0
    for signal in signals:
        i+=1
        print (i)
        # Initialize the cleaned signal
        signal= np.ravel(signal)
        signal_clean = signal.copy()
        # Compute the maximum absolute amplitude (MAA) for each sliding window
        while True:
            
            windows = [signal_clean[i:i+window_size] for i in range(0, len(signal_clean), window_size)]

            # Compute the maximum absolute amplitude (MAA) for each window
            maa = [np.max(np.abs(window)) for window in windows]
            
        
            # Compute the median MAA value
            median_maa = np.median(maa)
                    
            
            # Check if any MAA exceeds three times the median value of the MAA's

            if np.any(maa > 3 * median_maa):
                print ('entered')
                # Find the window with the highest MAA value
                max_maa_index  = np.argmax(maa)
                
                print (max_maa_index)
                spike_index = max_maa_index * window_size + np.argmax(np.abs(windows[max_maa_index]))
                
                print (spike_index)
                
                
                # Determine the first zero-crossing point after the spike index
                before_spike_index = spike_index -2 if spike_index>2 else 0
                after_spike_index  = spike_index +2 if len(signal)-spike_index>2 else len(signal)
                
                # Determine the last zero-crossing point before the spike index
               
                zero_crossings_before = np.where(np.diff(np.sign(signal[:before_spike_index])))[0]
                if len (zero_crossings_before)>0:
                    last_zero_crossing = zero_crossings_before[-1]
                else:
                    last_zero_crossing = 0
                    
                
                
                
                zero_crossings_after = np.where(np.diff(np.sign(signal[before_spike_index:])))[0]
                if len (zero_crossings_after)>0:
                    first_zero_crossing_after = zero_crossings_after[0] + spike_index
                else:
                    first_zero_crossing_after = len(signal_clean) - 1 
                # Replace the noise spike with zeros
                signal_clean[last_zero_crossing:first_zero_crossing_after +1] = 0
                print (last_zero_crossing,first_zero_crossing_after)
            else:
                print ('not entered')
                break
        filtered_signals.append(signal_clean)
    return np.array(filtered_signals)

In [27]:
# Since the signal is 300 Hz, the low pass portion (150 Hz) isnt applied since 300/2=150 (nyquist)
lowcut = 0.5
highcut = 100
fs = 300
order = 4


X_train_ecg = butter_bandpass(lowcut, highcut,  fs, order, X_train_ecg)
X_test_ecg = butter_bandpass(lowcut, highcut,  fs, order, X_test_ecg)
#X_train_ecg = remove_spikes(X_train_ecg, 0.5,300 )
#X_test_ecg = remove_spikes(X_test_ecg, 0.5, 300 )


1
not entered
2
not entered
3
not entered
4
not entered
5
not entered
6
not entered
7
not entered
8
not entered
9
not entered
10
not entered
11
not entered
12
not entered
13
not entered
14
not entered
15
not entered
16
not entered
17
not entered
18
not entered
19
not entered
20
not entered
21
not entered
22
not entered
23
not entered
24
not entered
25
not entered
26
not entered
27
not entered
28
not entered
29
not entered
30
not entered
31
not entered
32
not entered
33
not entered
34
not entered
35
not entered
36
not entered
37
not entered
38
not entered
39
not entered
40
entered
0
47
5 114
not entered
41
entered
2
349
329 449
not entered
42
entered
4
704
698 711
not entered
43
not entered
44
entered
3
551
542 565
not entered
45
not entered
46
not entered
47
not entered
48
not entered
49
not entered
50
not entered
51
not entered
52
not entered
53
not entered
54
not entered
55
not entered
56
not entered
57
not entered
58
not entered
59
not entered
60
not entered
61
not entered
62
not en

not entered
733
not entered
734
not entered
735
not entered
736
not entered
737
not entered
738
not entered
739
not entered
740
not entered
741
not entered
742
not entered
743
not entered
744
not entered
745
not entered
746
not entered
747
not entered
748
not entered
749
not entered
750
entered
6
942
934 952
entered
4
617
609 626
entered
8
1272
1264 1281
entered
1
274
267 282
not entered
751
not entered
752
not entered
753
not entered
754
not entered
755
not entered
756
not entered
757
not entered
758
not entered
759
not entered
760
not entered
761
not entered
762
not entered
763
not entered
764
not entered
765
not entered
766
entered
2
335
326 342
entered
9
1443
1434 1451
entered
4
702
693 709
entered
7
1068
1059 1076
not entered
767
entered
7
1064
1056 1072
entered
9
1438
1429 1446
entered
2
319
310 326
entered
4
692
684 700
not entered
768
entered
9
1401
1392 1409
entered
2
309
301 317
entered
4
675
666 682
entered
6
1036
1027 1043
not entered
769
entered
1
194
162 252
not entered
7

not entered
1479
entered
7
1131
1117 1154
not entered
1480
not entered
1481
not entered
1482
not entered
1483
not entered
1484
not entered
1485
not entered
1486
not entered
1487
not entered
1488
not entered
1489
not entered
1490
entered
2
321
178 340
entered
2
403
338 472
entered
3
496
470 626
not entered
1491
not entered
1492
not entered
1493
not entered
1494
not entered
1495
not entered
1496
not entered
1497
not entered
1498
not entered
1499
not entered
1500
not entered
1501
not entered
1502
not entered
1503
not entered
1504
not entered
1505
not entered
1506
not entered
1507
not entered
1508
not entered
1509
not entered
1510
not entered
1511
not entered
1512
not entered
1513
not entered
1514
not entered
1515
not entered
1516
not entered
1517
not entered
1518
not entered
1519
not entered
1520
not entered
1521
not entered
1522
not entered
1523
not entered
1524
not entered
1525
not entered
1526
not entered
1527
not entered
1528
not entered
1529
not entered
1530
not entered
1531
not ente

2183
not entered
2184
not entered
2185
not entered
2186
not entered
2187
not entered
2188
not entered
2189
not entered
2190
not entered
2191
not entered
2192
not entered
2193
not entered
2194
not entered
2195
not entered
2196
not entered
2197
not entered
2198
not entered
2199
not entered
2200
not entered
2201
not entered
2202
not entered
2203
entered
1
208
202 214
entered
3
542
536 548
entered
5
876
870 882
entered
7
1196
1190 1202
entered
8
1210
1200 1249
entered
1
222
212 293
entered
3
556
546 566
entered
5
889
880 907
entered
3
534
520 538
entered
5
867
852 872
entered
1
200
185 204
entered
7
1187
1171 1192
not entered
2204
not entered
2205
not entered
2206
not entered
2207
not entered
2208
not entered
2209
not entered
2210
not entered
2211
not entered
2212
not entered
2213
not entered
2214
not entered
2215
not entered
2216
not entered
2217
entered
9
1394
1390 1401
entered
4
647
643 661
entered
1
283
279 293
entered
6
1022
1018 1032
entered
9
1387
1240 1392
entered
4
641
525 645
ent

entered
5
889
869 903
entered
8
1275
1250 1292
not entered
2890
entered
5
772
695 786
not entered
2891
not entered
2892
entered
2
425
398 441
entered
0
36
0 53
not entered
2893
not entered
2894
not entered
2895
not entered
2896
not entered
2897
not entered
2898
not entered
2899
not entered
2900
not entered
2901
not entered
2902
not entered
2903
not entered
2904
not entered
2905
not entered
2906
not entered
2907
not entered
2908
not entered
2909
not entered
2910
not entered
2911
not entered
2912
not entered
2913
not entered
2914
not entered
2915
not entered
2916
not entered
2917
not entered
2918
not entered
2919
not entered
2920
not entered
2921
not entered
2922
not entered
2923
not entered
2924
not entered
2925
not entered
2926
not entered
2927
not entered
2928
not entered
2929
not entered
2930
not entered
2931
not entered
2932
not entered
2933
not entered
2934
not entered
2935
entered
0
41
0 70
not entered
2936
not entered
2937
not entered
2938
not entered
2939
not entered
2940
not en

...

not entered
13701
not entered
13702
not entered
13703
not entered
13704
not entered
13705
not entered
13706
not entered
13707
not entered
13708
not entered
13709
not entered
13710
not entered
13711
not entered
13712
not entered
13713
not entered
13714
not entered
13715
not entered
13716
not entered
13717
not entered
13718
not entered
13719
not entered
13720
entered
0
5
0 62
not entered
13721
not entered
13722
not entered
13723
not entered
13724
not entered
13725
not entered
13726
not entered
13727
not entered
13728
not entered
13729
not entered
13730
not entered
13731
not entered
13732
entered
0
117
98 165
entered
1
215
163 335
entered
0
16
0 80
not entered
13733
not entered
13734
not entered
13735
not entered
13736
not entered
13737
not entered
13738
not entered
13739
not entered
13740
not entered
13741
not entered
13742
not entered
13743
not entered
13744
entered
1
295
285 335
not entered
13745
not entered
13746
not entered
13747
not entered
13748
not entered
13749
not entered
13750


not entered
14439
not entered
14440
not entered
14441
not entered
14442
not entered
14443
not entered
14444
not entered
14445
not entered
14446
not entered
14447
not entered
14448
not entered
14449
entered
0
5
0 62
not entered
14450
not entered
14451
not entered
14452
not entered
14453
not entered
14454
not entered
14455
not entered
14456
not entered
14457
not entered
14458
not entered
14459
not entered
14460
not entered
14461
not entered
14462
not entered
14463
not entered
14464
not entered
14465
not entered
14466
not entered
14467
not entered
14468
not entered
14469
not entered
14470
entered
8
1239
1233 1245
entered
3
582
575 589
entered
6
917
900 923
entered
1
264
258 270
not entered
14471
not entered
14472
not entered
14473
not entered
14474
entered
0
147
132 176
not entered
14475
not entered
14476
entered
7
1189
1176 1203
entered
5
809
789 826
entered
2
434
404 448
entered
0
50
42 61
not entered
14477
not entered
14478
entered
7
1130
1121 1144
entered
4
747
737 760
entered
2
361
3

not entered
15096
not entered
15097
not entered
15098
not entered
15099
not entered
15100
not entered
15101
not entered
15102
not entered
15103
not entered
15104
not entered
15105
not entered
15106
not entered
15107
not entered
15108
not entered
15109
not entered
15110
not entered
15111
not entered
15112
not entered
15113
not entered
15114
not entered
15115
not entered
15116
not entered
15117
not entered
15118
entered
0
8
0 147
not entered
15119
not entered
15120
not entered
15121
not entered
15122
not entered
15123
not entered
15124
not entered
15125
not entered
15126
not entered
15127
not entered
15128
not entered
15129
not entered
15130
not entered
15131
not entered
15132
not entered
15133
not entered
15134
not entered
15135
not entered
15136
not entered
15137
not entered
15138
not entered
15139
not entered
15140
not entered
15141
not entered
15142
entered
9
1481
1477 1486
not entered
15143
not entered
15144
not entered
15145
not entered
15146
not entered
15147
not entered
15148
not

entered
2
387
378 394
not entered
15453
not entered
15454
not entered
15455
not entered
15456
not entered
15457
entered
4
644
637 651
entered
8
1261
1254 1267
entered
1
275
263 283
not entered
15458
not entered
15459
not entered
15460
not entered
15461
not entered
15462
not entered
15463
not entered
15464
not entered
15465
not entered
15466
not entered
15467
entered
2
376
352 396
entered
4
608
565 630
entered
2
431
394 567
not entered
15468
not entered
15469
not entered
15470
not entered
15471
not entered
15472
not entered
15473
not entered
15474
entered
5
862
848 869
entered
4
618
605 625
entered
1
282
270 290
entered
8
1281
1270 1288
not entered
15475
not entered
15476
entered
2
341
327 348
entered
9
1369
1359 1376
entered
4
687
676 694
entered
6
1031
1020 1038
entered
0
4
0 191
not entered
15477
not entered
15478
not entered
15479
not entered
15480
not entered
15481
not entered
15482
not entered
15483
not entered
15484
not entered
15485
not entered
15486
not entered
15487
not entere

not entered
15870
not entered
15871
entered
2
376
279 383
entered
7
1135
1104 1142
entered
0
66
59 71
not entered
15872
entered
7
1121
1113 1131
not entered
15873
not entered
15874
entered
5
875
859 882
entered
7
1067
1061 1072
not entered
15875
entered
2
314
294 320
not entered
15876
not entered
15877
entered
4
607
591 616
not entered
15878
not entered
15879
not entered
15880
not entered
15881
not entered
15882
not entered
15883
not entered
15884
not entered
15885
not entered
15886
not entered
15887
not entered
15888
not entered
15889
not entered
15890
not entered
15891
not entered
15892
not entered
15893
not entered
15894
not entered
15895
not entered
15896
not entered
15897
not entered
15898
not entered
15899
not entered
15900
not entered
15901
not entered
15902
not entered
15903
not entered
15904
not entered
15905
not entered
15906
not entered
15907
not entered
15908
not entered
15909
not entered
15910
not entered
15911
not entered
15912
not entered
15913
not entered
15914
not ente

In [28]:
X_test_ecg = X_test_ecg.reshape(X_test_ecg.shape[0], X_test_ecg.shape[1], 1)
X_train_ecg = X_train_ecg.reshape(X_train_ecg.shape[0], X_train_ecg.shape[1], 1)

In [36]:
f_y_train[2]

0

In [36]:
ecg_signal = X_test[20][0:10000]

In [37]:
plt.plot(ecg_signal)
#plt.axis('off')
plt.tick_params(
    axis='both', # changes apply to both x and y axes
    which='both', # both major and minor ticks are affected
    bottom=False, # ticks along the bottom edge are off
    top=False, # ticks along the top edge are off
    left=False, # ticks along the left edge are off
    right=False, # ticks along the right edge are off
    labelbottom=False, # labels along the bottom edge are off
    labelleft=False # labels along the left edge are off
)

plt.savefig('ecg.jpg', dpi=300)
plt.close()

In [39]:
def generate_wavelet(xcg,fs,scales, wav):

    #t = np.array(range(len(ecg)-1))/fs            # Timestamps of the ecg samples
    coef, freqs = pywt.cwt(xcg, scales, wav, sampling_period= 1/fs)
    #freqs = freqs * fs
    #print (freqs)
    return coef, freqs


def generate_wavelet_images(sig, record_id, classification, fs, wav, scales, directory, index, resample=True, vmax_q = 99):
    i = index

    records = []
    y = classification
    r = record_id
    x = sig.flatten()
    #reflecting the signal to alleviate boundary effects
    x_padded = np.concatenate(( x[::-1], x, x[::-1]))
    data, f = generate_wavelet(x_padded, fs,scales, wav )
    data = data[:, len(x):len(x)*2]
    data=np.abs(data)
    vmax = np.percentile(data,vmax_q)
    vmin = np.abs(data).min()
    cmap = plt.get_cmap('jet', 128)
    #print (data.shape)
    #Padding to
    #
    print(data.shape)
    #print (data.shape)
    #plt.figure(figsize=(9,5))
    #print (data.shape)
    fig = matplotlib.pyplot.figure(figsize=(4, 3))
    ax = fig.add_subplot(111)
    t = np.arange(data.shape[1]) / fs  # Timestamps of the ECG samples
    if resample:
        data = data[:, ::5]
    plt.imshow(data, cmap=cmap, aspect ='auto', vmax=vmax, vmin=vmin, interpolation = 'None', origin = 'upper')

    #ax.set_yscale('log')
    ax.axis('off')
    fig.savefig(directory+'\\'+str(r)+'_'+str(i)+'.tiff', pad_inches=0, bbox_inches='tight', dpi=100 )
    #plt.close('all')
    matplotlib.pyplot.close(fig)
    #plt.ioff()

    image_dict = {'filename':str(r)+'_'+str(i)+'.tiff','label':y }
    print (str(r)+'_'+str(i)+'.tiff')

    return image_dict

In [62]:
fig, (ax1, ax2) = plt.subplots(1, 2)

t = np.linspace(0, len(X_train_ecg[2])/fs, len(X_train_ecg[2]))
ecg_signal = X_train_ecg[2]/5

ax1.plot(t, ecg_signal)
ax1.set_ylabel('Voltage (mV)')
ax1.set_xlabel('Time (s)')


wav = pywt.ContinuousWavelet("cmor1.5-1.0")
scales = np.arange(3, 100)
coef, freqs = generate_wavelet(ecg_signal.flatten(), 300,scales, wav)
print(t)
print(freqs)
print (len(np.abs(coef)))
t = np.arange(len(ecg_signal)) / fs  # Timestamps of the ECG samples

ax2.pcolormesh( t, freqs, np.abs(coef), cmap ='jet')
ax1.text(0.5,-0.2, "(a)", size=12, ha="center", 
         transform=ax1.transAxes)
ax2.text(0.5,-0.2, "(b)", size=12, ha="center", 
         transform=ax2.transAxes)

fig.tight_layout()

ax2.set_xlabel('Time (s)')
ax2.set_ylabel('Frequency (Hz)')
ax2.set_yscale('log')



fig.set_size_inches(10, 5)


plt.savefig('test_ecg.png', dpi=300)
plt.close()

[0.00000000e+00 3.33555704e-03 6.67111408e-03 ... 4.99332889e+00
 4.99666444e+00 5.00000000e+00]
[100.          75.          60.          50.          42.85714286
  37.5         33.33333333  30.          27.27272727  25.
  23.07692308  21.42857143  20.          18.75        17.64705882
  16.66666667  15.78947368  15.          14.28571429  13.63636364
  13.04347826  12.5         12.          11.53846154  11.11111111
  10.71428571  10.34482759  10.           9.67741935   9.375
   9.09090909   8.82352941   8.57142857   8.33333333   8.10810811
   7.89473684   7.69230769   7.5          7.31707317   7.14285714
   6.97674419   6.81818182   6.66666667   6.52173913   6.38297872
   6.25         6.12244898   6.           5.88235294   5.76923077
   5.66037736   5.55555556   5.45454545   5.35714286   5.26315789
   5.17241379   5.08474576   5.           4.91803279   4.83870968
   4.76190476   4.6875       4.61538462   4.54545455   4.47761194
   4.41176471   4.34782609   4.28571429   4.22535211   4.1

<ipython-input-62-adc2ee706132>:19: MatplotlibDeprecationWarning: shading='flat' when X and Y have the same dimensions as C is deprecated since 3.3.  Either specify the corners of the quadrilaterals with X and Y, or pass shading='auto', 'nearest' or 'gouraud', or set rcParams['pcolor.shading'].  This will become an error two minor releases later.
  ax2.pcolormesh( t, freqs, np.abs(coef), cmap ='jet')


In [32]:

if __name__ == '__main__':
    fs = 300
    wav = pywt.ContinuousWavelet("cmor1.5-1.0")
    scales = np.arange(3, 100)
    directory = 'physionet2017_ecg_scalograms\\test'
    record_ecg_test_list = []

    with concurrent.futures.ProcessPoolExecutor(12) as executor:
            futures = [executor.submit(gen_wav, sig, r ,y, fs, wav, scales, directory, i, False, 95) for sig,r, y,i in  zip(X_test_ecg, record_id_test, f_y_test, range(len(X_test_ecg)))]
            for future in concurrent.futures.as_completed(futures):
                print (future.result())
                record_ecg_test_list.append(future.result())
            

    df = pd.DataFrame(record_ecg_test_list)
    df.to_csv(directory+'\\dataset.csv')   

{'filename': 'A01975_6.tiff', 'label': 0}
{'filename': 'A01975_8.tiff', 'label': 0}
{'filename': 'A01975_0.tiff', 'label': 0}
{'filename': 'A01975_11.tiff', 'label': 0}
{'filename': 'A01975_4.tiff', 'label': 0}
{'filename': 'A01975_7.tiff', 'label': 0}
{'filename': 'A01975_1.tiff', 'label': 0}
{'filename': 'A01975_9.tiff', 'label': 0}
{'filename': 'A01975_10.tiff', 'label': 0}
{'filename': 'A01975_5.tiff', 'label': 0}
{'filename': 'A01975_2.tiff', 'label': 0}
{'filename': 'A01975_3.tiff', 'label': 0}
{'filename': 'A07376_16.tiff', 'label': 0}
{'filename': 'A07376_13.tiff', 'label': 0}
{'filename': 'A07376_14.tiff', 'label': 0}
{'filename': 'A07376_15.tiff', 'label': 0}
{'filename': 'A07376_12.tiff', 'label': 0}
{'filename': 'A07376_17.tiff', 'label': 0}
{'filename': 'A01132_19.tiff', 'label': 0}
{'filename': 'A01132_20.tiff', 'label': 0}
{'filename': 'A01132_18.tiff', 'label': 0}
{'filename': 'A01132_23.tiff', 'label': 0}
{'filename': 'A01132_22.tiff', 'label': 0}
{'filename': 'A01132_

{'filename': 'A04726_195.tiff', 'label': 0}
{'filename': 'A04726_194.tiff', 'label': 0}
{'filename': 'A04726_193.tiff', 'label': 0}
{'filename': 'A04726_192.tiff', 'label': 0}
{'filename': 'A04726_196.tiff', 'label': 0}
{'filename': 'A04726_197.tiff', 'label': 0}
{'filename': 'A05761_198.tiff', 'label': 0}
{'filename': 'A05761_199.tiff', 'label': 0}
{'filename': 'A05761_200.tiff', 'label': 0}
{'filename': 'A05761_201.tiff', 'label': 0}
{'filename': 'A05761_202.tiff', 'label': 0}
{'filename': 'A02869_205.tiff', 'label': 0}
{'filename': 'A05761_204.tiff', 'label': 0}
{'filename': 'A02869_206.tiff', 'label': 0}
{'filename': 'A02869_207.tiff', 'label': 0}
{'filename': 'A05761_203.tiff', 'label': 0}
{'filename': 'A02869_209.tiff', 'label': 0}
{'filename': 'A02869_210.tiff', 'label': 0}
{'filename': 'A05914_213.tiff', 'label': 0}
{'filename': 'A02869_208.tiff', 'label': 0}
{'filename': 'A05914_212.tiff', 'label': 0}
{'filename': 'A05914_215.tiff', 'label': 0}
{'filename': 'A05914_211.tiff', 

{'filename': 'A05608_386.tiff', 'label': 1}
{'filename': 'A06690_389.tiff', 'label': 1}
{'filename': 'A06690_387.tiff', 'label': 1}
{'filename': 'A06690_392.tiff', 'label': 1}
{'filename': 'A06690_390.tiff', 'label': 1}
{'filename': 'A06690_393.tiff', 'label': 1}
{'filename': 'A06690_395.tiff', 'label': 1}
{'filename': 'A06690_391.tiff', 'label': 1}
{'filename': 'A06690_394.tiff', 'label': 1}
{'filename': 'A06690_396.tiff', 'label': 1}
{'filename': 'A01491_398.tiff', 'label': 1}
{'filename': 'A01491_400.tiff', 'label': 1}
{'filename': 'A01491_397.tiff', 'label': 1}
{'filename': 'A01491_399.tiff', 'label': 1}
{'filename': 'A07163_404.tiff', 'label': 1}
{'filename': 'A07163_403.tiff', 'label': 1}
{'filename': 'A01491_401.tiff', 'label': 1}
{'filename': 'A07163_405.tiff', 'label': 1}
{'filename': 'A07163_408.tiff', 'label': 1}
{'filename': 'A01491_402.tiff', 'label': 1}
{'filename': 'A07163_407.tiff', 'label': 1}
{'filename': 'A07163_406.tiff', 'label': 1}
{'filename': 'A03963_409.tiff', 

{'filename': 'A08012_580.tiff', 'label': 1}
{'filename': 'A08012_583.tiff', 'label': 1}
{'filename': 'A08012_584.tiff', 'label': 1}
{'filename': 'A08012_582.tiff', 'label': 1}
{'filename': 'A08012_587.tiff', 'label': 1}
{'filename': 'A03911_589.tiff', 'label': 0}
{'filename': 'A08012_586.tiff', 'label': 1}
{'filename': 'A08012_585.tiff', 'label': 1}
{'filename': 'A03911_591.tiff', 'label': 0}
{'filename': 'A08012_588.tiff', 'label': 1}
{'filename': 'A03911_590.tiff', 'label': 0}
{'filename': 'A01376_593.tiff', 'label': 1}
{'filename': 'A03911_592.tiff', 'label': 0}
{'filename': 'A01376_594.tiff', 'label': 1}
{'filename': 'A01376_595.tiff', 'label': 1}
{'filename': 'A01376_597.tiff', 'label': 1}
{'filename': 'A01376_596.tiff', 'label': 1}
{'filename': 'A06343_599.tiff', 'label': 1}
{'filename': 'A01376_598.tiff', 'label': 1}
{'filename': 'A06343_602.tiff', 'label': 1}
{'filename': 'A06343_600.tiff', 'label': 1}
{'filename': 'A06343_603.tiff', 'label': 1}
{'filename': 'A06343_601.tiff', 

{'filename': 'A02946_772.tiff', 'label': 0}
{'filename': 'A02946_774.tiff', 'label': 0}
{'filename': 'A08312_775.tiff', 'label': 1}
{'filename': 'A02946_771.tiff', 'label': 0}
{'filename': 'A08312_776.tiff', 'label': 1}
{'filename': 'A08312_779.tiff', 'label': 1}
{'filename': 'A02946_773.tiff', 'label': 0}
{'filename': 'A08312_778.tiff', 'label': 1}
{'filename': 'A08312_780.tiff', 'label': 1}
{'filename': 'A08312_777.tiff', 'label': 1}
{'filename': 'A08140_782.tiff', 'label': 0}
{'filename': 'A08140_783.tiff', 'label': 0}
{'filename': 'A08140_784.tiff', 'label': 0}
{'filename': 'A08140_785.tiff', 'label': 0}
{'filename': 'A08210_791.tiff', 'label': 1}
{'filename': 'A08140_781.tiff', 'label': 0}
{'filename': 'A08210_789.tiff', 'label': 1}
{'filename': 'A08210_790.tiff', 'label': 1}
{'filename': 'A08210_787.tiff', 'label': 1}
{'filename': 'A07722_793.tiff', 'label': 1}
{'filename': 'A08210_788.tiff', 'label': 1}
{'filename': 'A07722_794.tiff', 'label': 1}
{'filename': 'A07722_795.tiff', 

...

{'filename': 'A00641_15054.tiff', 'label': 0}
{'filename': 'A00663_15057.tiff', 'label': 0}
{'filename': 'A00641_15049.tiff', 'label': 0}
{'filename': 'A00663_15056.tiff', 'label': 0}
{'filename': 'A00641_15052.tiff', 'label': 0}
{'filename': 'A00663_15055.tiff', 'label': 0}
{'filename': 'A00641_15053.tiff', 'label': 0}
{'filename': 'A00663_15059.tiff', 'label': 0}
{'filename': 'A00663_15060.tiff', 'label': 0}
{'filename': 'A05131_15061.tiff', 'label': 0}
{'filename': 'A00663_15058.tiff', 'label': 0}
{'filename': 'A05131_15062.tiff', 'label': 0}
{'filename': 'A05131_15063.tiff', 'label': 0}
{'filename': 'A05131_15064.tiff', 'label': 0}
{'filename': 'A08364_15065.tiff', 'label': 0}
{'filename': 'A08364_15068.tiff', 'label': 0}
{'filename': 'A08364_15067.tiff', 'label': 0}
{'filename': 'A08364_15066.tiff', 'label': 0}
{'filename': 'A08364_15069.tiff', 'label': 0}
{'filename': 'A02333_15074.tiff', 'label': 1}
{'filename': 'A02333_15073.tiff', 'label': 1}
{'filename': 'A02333_15071.tiff', 

{'filename': 'A05905_15239.tiff', 'label': 0}
{'filename': 'A05905_15240.tiff', 'label': 0}
{'filename': 'A05905_15238.tiff', 'label': 0}
{'filename': 'A05905_15242.tiff', 'label': 0}
{'filename': 'A05905_15237.tiff', 'label': 0}
{'filename': 'A05905_15241.tiff', 'label': 0}
{'filename': 'A03823_15244.tiff', 'label': 0}
{'filename': 'A03823_15245.tiff', 'label': 0}
{'filename': 'A03823_15243.tiff', 'label': 0}
{'filename': 'A03823_15248.tiff', 'label': 0}
{'filename': 'A03823_15247.tiff', 'label': 0}
{'filename': 'A03823_15246.tiff', 'label': 0}
{'filename': 'A06686_15250.tiff', 'label': 0}
{'filename': 'A06686_15252.tiff', 'label': 0}
{'filename': 'A06686_15254.tiff', 'label': 0}
{'filename': 'A06686_15251.tiff', 'label': 0}
{'filename': 'A06686_15249.tiff', 'label': 0}
{'filename': 'A06686_15255.tiff', 'label': 0}
{'filename': 'A06686_15253.tiff', 'label': 0}
{'filename': 'A06686_15256.tiff', 'label': 0}
{'filename': 'A06686_15257.tiff', 'label': 0}
{'filename': 'A06686_15259.tiff', 

{'filename': 'A06994_15426.tiff', 'label': 0}
{'filename': 'A06994_15427.tiff', 'label': 0}
{'filename': 'A08387_15428.tiff', 'label': 0}
{'filename': 'A08387_15430.tiff', 'label': 0}
{'filename': 'A02352_15434.tiff', 'label': 0}
{'filename': 'A08387_15431.tiff', 'label': 0}
{'filename': 'A08387_15429.tiff', 'label': 0}
{'filename': 'A08387_15433.tiff', 'label': 0}
{'filename': 'A08387_15432.tiff', 'label': 0}
{'filename': 'A02352_15435.tiff', 'label': 0}
{'filename': 'A02352_15436.tiff', 'label': 0}
{'filename': 'A02352_15438.tiff', 'label': 0}
{'filename': 'A02352_15437.tiff', 'label': 0}
{'filename': 'A02960_15440.tiff', 'label': 0}
{'filename': 'A02352_15439.tiff', 'label': 0}
{'filename': 'A02960_15442.tiff', 'label': 0}
{'filename': 'A02960_15443.tiff', 'label': 0}
{'filename': 'A02960_15441.tiff', 'label': 0}
{'filename': 'A02960_15445.tiff', 'label': 0}
{'filename': 'A02960_15444.tiff', 'label': 0}
{'filename': 'A04973_15446.tiff', 'label': 1}
{'filename': 'A04973_15447.tiff', 

{'filename': 'A01631_15605.tiff', 'label': 0}
{'filename': 'A01631_15607.tiff', 'label': 0}
{'filename': 'A01631_15609.tiff', 'label': 0}
{'filename': 'A01631_15606.tiff', 'label': 0}
{'filename': 'A01631_15608.tiff', 'label': 0}
{'filename': 'A01631_15610.tiff', 'label': 0}
{'filename': 'A01771_15614.tiff', 'label': 0}
{'filename': 'A01771_15613.tiff', 'label': 0}
{'filename': 'A01771_15612.tiff', 'label': 0}
{'filename': 'A01771_15615.tiff', 'label': 0}
{'filename': 'A01771_15616.tiff', 'label': 0}
{'filename': 'A01771_15611.tiff', 'label': 0}
{'filename': 'A01771_15617.tiff', 'label': 0}
{'filename': 'A01771_15619.tiff', 'label': 0}
{'filename': 'A01771_15618.tiff', 'label': 0}
{'filename': 'A01771_15620.tiff', 'label': 0}
{'filename': 'A01771_15622.tiff', 'label': 0}
{'filename': 'A01771_15621.tiff', 'label': 0}
{'filename': 'A05114_15623.tiff', 'label': 0}
{'filename': 'A05114_15627.tiff', 'label': 0}
{'filename': 'A05114_15626.tiff', 'label': 0}
{'filename': 'A05114_15624.tiff', 

{'filename': 'A05229_15787.tiff', 'label': 0}
{'filename': 'A05229_15789.tiff', 'label': 0}
{'filename': 'A05229_15788.tiff', 'label': 0}
{'filename': 'A05229_15786.tiff', 'label': 0}
{'filename': 'A05229_15790.tiff', 'label': 0}
{'filename': 'A05229_15791.tiff', 'label': 0}
{'filename': 'A04667_15793.tiff', 'label': 1}
{'filename': 'A04667_15792.tiff', 'label': 1}
{'filename': 'A03395_15794.tiff', 'label': 0}
{'filename': 'A03395_15796.tiff', 'label': 0}
{'filename': 'A03395_15797.tiff', 'label': 0}
{'filename': 'A03395_15795.tiff', 'label': 0}
{'filename': 'A03395_15799.tiff', 'label': 0}
{'filename': 'A03395_15798.tiff', 'label': 0}
{'filename': 'A04791_15803.tiff', 'label': 0}
{'filename': 'A04791_15800.tiff', 'label': 0}
{'filename': 'A04791_15804.tiff', 'label': 0}
{'filename': 'A04791_15802.tiff', 'label': 0}
{'filename': 'A04791_15801.tiff', 'label': 0}
{'filename': 'A04791_15805.tiff', 'label': 0}
{'filename': 'A06562_15808.tiff', 'label': 1}
{'filename': 'A06562_15809.tiff', 

In [33]:

if __name__ == '__main__':
    fs = 300
    wav = pywt.ContinuousWavelet("cmor1.5-1.0")
    scales = np.arange(3, 100)
    directory = 'physionet2017_ecg_scalograms\\train'
    record_ecg_test_list = []

    with concurrent.futures.ProcessPoolExecutor(12) as executor:
            futures = [executor.submit(gen_wav, sig, r ,y, fs, wav, scales, directory, i, False, 95) for sig,r, y,i in  zip(X_train_ecg, record_id, f_y_train, range(len(X_train_ecg)))]
            for future in concurrent.futures.as_completed(futures):
                print (future.result())
                record_ecg_test_list.append(future.result())
            

    df = pd.DataFrame(record_ecg_test_list)
    df.to_csv(directory+'\\dataset.csv')   


{'filename': 'A06729_11.tiff', 'label': 0}
{'filename': 'A06047_4.tiff', 'label': 0}
{'filename': 'A01326_149.tiff', 'label': 1}
{'filename': 'A02351_69.tiff', 'label': 0}
{'filename': 'A03493_22.tiff', 'label': 1}
{'filename': 'A04068_116.tiff', 'label': 0}
{'filename': 'A01326_148.tiff', 'label': 1}
{'filename': 'A08357_104.tiff', 'label': 0}
{'filename': 'A05279_64.tiff', 'label': 0}
{'filename': 'A01440_107.tiff', 'label': 0}
{'filename': 'A06792_143.tiff', 'label': 0}
{'filename': 'A01440_110.tiff', 'label': 0}
{'filename': 'A08155_113.tiff', 'label': 0}
{'filename': 'A05307_122.tiff', 'label': 0}
{'filename': 'A07548_140.tiff', 'label': 0}
{'filename': 'A06066_49.tiff', 'label': 0}
{'filename': 'A06792_147.tiff', 'label': 0}
{'filename': 'A04404_79.tiff', 'label': 0}
{'filename': 'A02642_17.tiff', 'label': 0}
{'filename': 'A06047_3.tiff', 'label': 0}
{'filename': 'A06269_138.tiff', 'label': 1}
{'filename': 'A04471_60.tiff', 'label': 1}
{'filename': 'A06066_44.tiff', 'label': 0}
{

{'filename': 'A05988_191.tiff', 'label': 0}
{'filename': 'A05988_192.tiff', 'label': 0}
{'filename': 'A03899_197.tiff', 'label': 0}
{'filename': 'A03899_194.tiff', 'label': 0}
{'filename': 'A03899_196.tiff', 'label': 0}
{'filename': 'A03899_195.tiff', 'label': 0}
{'filename': 'A03899_199.tiff', 'label': 0}
{'filename': 'A03899_198.tiff', 'label': 0}
{'filename': 'A03194_200.tiff', 'label': 0}
{'filename': 'A03194_201.tiff', 'label': 0}
{'filename': 'A06203_203.tiff', 'label': 1}
{'filename': 'A06203_205.tiff', 'label': 1}
{'filename': 'A06203_202.tiff', 'label': 1}
{'filename': 'A06203_207.tiff', 'label': 1}
{'filename': 'A06203_206.tiff', 'label': 1}
{'filename': 'A06203_204.tiff', 'label': 1}
{'filename': 'A00845_211.tiff', 'label': 0}
{'filename': 'A00845_209.tiff', 'label': 0}
{'filename': 'A00845_208.tiff', 'label': 0}
{'filename': 'A00845_212.tiff', 'label': 0}
{'filename': 'A00845_210.tiff', 'label': 0}
{'filename': 'A00845_213.tiff', 'label': 0}
{'filename': 'A07141_215.tiff', 

{'filename': 'A00895_383.tiff', 'label': 0}
{'filename': 'A00895_384.tiff', 'label': 0}
{'filename': 'A04850_386.tiff', 'label': 0}
{'filename': 'A04850_387.tiff', 'label': 0}
{'filename': 'A04850_385.tiff', 'label': 0}
{'filename': 'A04850_388.tiff', 'label': 0}
{'filename': 'A04850_390.tiff', 'label': 0}
{'filename': 'A04850_389.tiff', 'label': 0}
{'filename': 'A08321_392.tiff', 'label': 0}
{'filename': 'A08321_394.tiff', 'label': 0}
{'filename': 'A08321_391.tiff', 'label': 0}
{'filename': 'A00627_397.tiff', 'label': 0}
{'filename': 'A08321_393.tiff', 'label': 0}
{'filename': 'A08321_395.tiff', 'label': 0}
{'filename': 'A08321_396.tiff', 'label': 0}
{'filename': 'A00627_398.tiff', 'label': 0}
{'filename': 'A00627_399.tiff', 'label': 0}
{'filename': 'A00627_402.tiff', 'label': 0}
{'filename': 'A00627_401.tiff', 'label': 0}
{'filename': 'A00627_400.tiff', 'label': 0}
{'filename': 'A00627_403.tiff', 'label': 0}
{'filename': 'A04407_408.tiff', 'label': 1}
{'filename': 'A00627_405.tiff', 

{'filename': 'A05818_572.tiff', 'label': 1}
{'filename': 'A05818_571.tiff', 'label': 1}
{'filename': 'A05291_578.tiff', 'label': 0}
{'filename': 'A05291_576.tiff', 'label': 0}
{'filename': 'A05291_577.tiff', 'label': 0}
{'filename': 'A05291_579.tiff', 'label': 0}
{'filename': 'A08510_580.tiff', 'label': 1}
{'filename': 'A08510_582.tiff', 'label': 1}
{'filename': 'A08510_581.tiff', 'label': 1}
{'filename': 'A08510_583.tiff', 'label': 1}
{'filename': 'A08510_584.tiff', 'label': 1}
{'filename': 'A08510_585.tiff', 'label': 1}
{'filename': 'A04399_586.tiff', 'label': 0}
{'filename': 'A04399_587.tiff', 'label': 0}
{'filename': 'A04399_588.tiff', 'label': 0}
{'filename': 'A04399_589.tiff', 'label': 0}
{'filename': 'A05614_592.tiff', 'label': 1}
{'filename': 'A04399_590.tiff', 'label': 0}
{'filename': 'A04399_591.tiff', 'label': 0}
{'filename': 'A05614_594.tiff', 'label': 1}
{'filename': 'A05614_593.tiff', 'label': 1}
{'filename': 'A05614_595.tiff', 'label': 1}
{'filename': 'A05614_597.tiff', 

{'filename': 'A00243_764.tiff', 'label': 1}
{'filename': 'A00243_763.tiff', 'label': 1}
{'filename': 'A00243_766.tiff', 'label': 1}
{'filename': 'A00243_765.tiff', 'label': 1}
{'filename': 'A00243_767.tiff', 'label': 1}
{'filename': 'A06017_769.tiff', 'label': 0}
{'filename': 'A06017_771.tiff', 'label': 0}
{'filename': 'A06017_770.tiff', 'label': 0}
{'filename': 'A06017_768.tiff', 'label': 0}
{'filename': 'A06017_772.tiff', 'label': 0}
{'filename': 'A06017_773.tiff', 'label': 0}
{'filename': 'A04204_774.tiff', 'label': 0}
{'filename': 'A01639_776.tiff', 'label': 1}
{'filename': 'A01639_778.tiff', 'label': 1}
{'filename': 'A01639_779.tiff', 'label': 1}
{'filename': 'A01639_777.tiff', 'label': 1}
{'filename': 'A04204_775.tiff', 'label': 0}
{'filename': 'A01639_781.tiff', 'label': 1}
{'filename': 'A01754_782.tiff', 'label': 0}
{'filename': 'A01639_780.tiff', 'label': 1}
{'filename': 'A01754_784.tiff', 'label': 0}
{'filename': 'A01754_783.tiff', 'label': 0}
{'filename': 'A01754_785.tiff', 

...

{'filename': 'A01873_36575.tiff', 'label': 1}
{'filename': 'A01873_36577.tiff', 'label': 1}
{'filename': 'A07951_36580.tiff', 'label': 0}
{'filename': 'A01873_36579.tiff', 'label': 1}
{'filename': 'A01873_36578.tiff', 'label': 1}
{'filename': 'A01873_36576.tiff', 'label': 1}
{'filename': 'A07951_36582.tiff', 'label': 0}
{'filename': 'A07951_36581.tiff', 'label': 0}
{'filename': 'A07951_36583.tiff', 'label': 0}
{'filename': 'A07951_36584.tiff', 'label': 0}
{'filename': 'A07951_36585.tiff', 'label': 0}
{'filename': 'A00538_36586.tiff', 'label': 0}
{'filename': 'A00538_36588.tiff', 'label': 0}
{'filename': 'A00538_36591.tiff', 'label': 0}
{'filename': 'A00538_36589.tiff', 'label': 0}
{'filename': 'A00538_36590.tiff', 'label': 0}
{'filename': 'A00538_36587.tiff', 'label': 0}
{'filename': 'A07935_36592.tiff', 'label': 0}
{'filename': 'A07935_36593.tiff', 'label': 0}
{'filename': 'A07935_36594.tiff', 'label': 0}
{'filename': 'A07935_36597.tiff', 'label': 0}
{'filename': 'A07935_36596.tiff', 

{'filename': 'A00508_36753.tiff', 'label': 0}
{'filename': 'A03080_36755.tiff', 'label': 1}
{'filename': 'A03080_36756.tiff', 'label': 1}
{'filename': 'A03080_36757.tiff', 'label': 1}
{'filename': 'A03080_36758.tiff', 'label': 1}
{'filename': 'A03080_36760.tiff', 'label': 1}
{'filename': 'A03080_36759.tiff', 'label': 1}
{'filename': 'A03080_36762.tiff', 'label': 1}
{'filename': 'A03080_36761.tiff', 'label': 1}
{'filename': 'A03080_36765.tiff', 'label': 1}
{'filename': 'A03080_36763.tiff', 'label': 1}
{'filename': 'A03080_36764.tiff', 'label': 1}
{'filename': 'A07414_36766.tiff', 'label': 0}
{'filename': 'A07414_36767.tiff', 'label': 0}
{'filename': 'A07414_36768.tiff', 'label': 0}
{'filename': 'A07414_36769.tiff', 'label': 0}
{'filename': 'A07414_36770.tiff', 'label': 0}
{'filename': 'A07414_36775.tiff', 'label': 0}
{'filename': 'A07414_36771.tiff', 'label': 0}
{'filename': 'A07414_36772.tiff', 'label': 0}
{'filename': 'A07414_36774.tiff', 'label': 0}
{'filename': 'A07414_36773.tiff', 

{'filename': 'A00712_36942.tiff', 'label': 1}
{'filename': 'A00712_36947.tiff', 'label': 1}
{'filename': 'A00712_36944.tiff', 'label': 1}
{'filename': 'A00712_36945.tiff', 'label': 1}
{'filename': 'A00712_36943.tiff', 'label': 1}
{'filename': 'A00712_36946.tiff', 'label': 1}
{'filename': 'A00712_36948.tiff', 'label': 1}
{'filename': 'A00414_36950.tiff', 'label': 0}
{'filename': 'A00414_36952.tiff', 'label': 0}
{'filename': 'A00414_36951.tiff', 'label': 0}
{'filename': 'A00712_36949.tiff', 'label': 1}
{'filename': 'A00414_36953.tiff', 'label': 0}
{'filename': 'A00414_36954.tiff', 'label': 0}
{'filename': 'A01781_36955.tiff', 'label': 0}
{'filename': 'A01781_36956.tiff', 'label': 0}
{'filename': 'A01121_36958.tiff', 'label': 0}
{'filename': 'A01121_36960.tiff', 'label': 0}
{'filename': 'A03150_36961.tiff', 'label': 0}
{'filename': 'A01121_36957.tiff', 'label': 0}
{'filename': 'A01121_36959.tiff', 'label': 0}
{'filename': 'A03150_36962.tiff', 'label': 0}
{'filename': 'A06837_36964.tiff', 

{'filename': 'A07777_37127.tiff', 'label': 1}
{'filename': 'A07777_37129.tiff', 'label': 1}
{'filename': 'A07777_37130.tiff', 'label': 1}
{'filename': 'A07777_37128.tiff', 'label': 1}
{'filename': 'A07777_37131.tiff', 'label': 1}
{'filename': 'A07777_37135.tiff', 'label': 1}
{'filename': 'A07777_37134.tiff', 'label': 1}
{'filename': 'A07777_37132.tiff', 'label': 1}
{'filename': 'A07777_37133.tiff', 'label': 1}
{'filename': 'A00394_37137.tiff', 'label': 1}
{'filename': 'A07364_37138.tiff', 'label': 0}
{'filename': 'A00394_37136.tiff', 'label': 1}
{'filename': 'A07364_37139.tiff', 'label': 0}
{'filename': 'A07364_37143.tiff', 'label': 0}
{'filename': 'A07364_37142.tiff', 'label': 0}
{'filename': 'A02635_37144.tiff', 'label': 0}
{'filename': 'A07364_37140.tiff', 'label': 0}
{'filename': 'A02635_37145.tiff', 'label': 0}
{'filename': 'A07364_37141.tiff', 'label': 0}
{'filename': 'A02635_37147.tiff', 'label': 0}
{'filename': 'A02635_37146.tiff', 'label': 0}
{'filename': 'A01487_37150.tiff', 

{'filename': 'A01704_37311.tiff', 'label': 0}
{'filename': 'A01704_37314.tiff', 'label': 0}
{'filename': 'A01704_37313.tiff', 'label': 0}
{'filename': 'A07279_37317.tiff', 'label': 0}
{'filename': 'A07279_37315.tiff', 'label': 0}
{'filename': 'A07279_37316.tiff', 'label': 0}
{'filename': 'A07279_37319.tiff', 'label': 0}
{'filename': 'A07279_37320.tiff', 'label': 0}
{'filename': 'A07279_37318.tiff', 'label': 0}
{'filename': 'A04389_37321.tiff', 'label': 0}
{'filename': 'A04389_37322.tiff', 'label': 0}
{'filename': 'A04389_37323.tiff', 'label': 0}
{'filename': 'A04389_37324.tiff', 'label': 0}
{'filename': 'A04389_37325.tiff', 'label': 0}
{'filename': 'A04389_37326.tiff', 'label': 0}
{'filename': 'A04389_37328.tiff', 'label': 0}
{'filename': 'A04389_37329.tiff', 'label': 0}
{'filename': 'A04389_37327.tiff', 'label': 0}
{'filename': 'A04389_37330.tiff', 'label': 0}
{'filename': 'A04389_37331.tiff', 'label': 0}
{'filename': 'A04389_37332.tiff', 'label': 0}
{'filename': 'A03260_37334.tiff', 

In [ ]:

def butter_bandpass(lowcut, highcut, fs, order, signals):
    # Normalized cutoff frequencies
    b, a = scipy.signal.butter(order, [lowcut, highcut], btype='band', fs=fs)
    
    filtered_signals = []
    for s in signals:
        s= np.ravel(s)
        #print (s.shape)
        y = scipy.signal.filtfilt(b, a, s)
        
        filtered_signals.append(y)
    return np.array(filtered_signals)


In [50]:
b, a = scipy.signal.butter(4, [0.5, 100], btype='band', fs=2000)
w, h = scipy.signal.freqs(b, a)
plt.semilogx(w, 20 * np.log10(abs(h)))
plt.title('Butterworth filter frequency response')
plt.xlabel('Frequency [radians / second]')
plt.ylabel('Amplitude [dB]')
plt.margins(0, 0.1)
plt.grid(which='both', axis='both')
plt.axvline(100, color='green') # cutoff frequency
plt.savefig('freq_response_butterworth.png')
plt.show()
plt.close()

<ipython-input-50-cacdf5f0b1dd>:11: UserWarning: Matplotlib is currently using agg, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [53]:
b, a = scipy.signal.butter(4, [50, 100], btype='band', fs=2000)

# Calculate the frequency response
w, h = scipy.signal.freqz(b, a)

# Calculate the frequency axis in Hz
freq = w * 1000 / (2 * np.pi)

# Plot the frequency response
plt.figure(figsize=(10, 6))
plt.plot(freq, 20 * np.log10(np.abs(h)), 'b')
plt.title('Butterworth Bandpass Filter Frequency Response')
plt.xlabel('Frequency (Hz)')
plt.ylabel('Gain (dB)')
plt.grid(True)
plt.savefig('freq_response_butterworth.png')
plt.show()
plt.close()

<ipython-input-53-f839787ddc57>:17: UserWarning: Matplotlib is currently using agg, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [68]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import signal

# Define the filter coefficients
b, a = signal.butter(4, [25, 400], btype='band', fs=2000)

# Calculate the frequency response
w, h = signal.freqz(b, a)

# Calculate the frequency axis in Hz
freq = w * 2000 / (2 * np.pi)  # Use fs = 2000 here

# Plot the frequency response
plt.figure(figsize=(10, 6))
plt.plot(freq, 20 * np.log10(np.abs(h)), 'b')
plt.title('Butterworth Bandpass Filter Frequency Response')
plt.xlabel('Frequency (Hz)')
plt.ylabel('Gain (dB)')
plt.xlim(0,1000)
#plt.ylim(-2, 1)
#plt.grid(True)
plt.savefig('freq_response_butterworth_pcg.png')

plt.show()

<ipython-input-68-580e0005596e>:25: UserWarning: Matplotlib is currently using agg, which is a non-GUI backend, so cannot show the figure.
  plt.show()
